[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/sebascarag/AI-SyntheticSound/blob/main/optuna-urbansound8k-vae.ipynb)

https://siddhartha01writes.medium.com/gpu-t4-vs-gpu-p100-kaggle-gpu-cd852d56022c

TPU P100 Should be used for training and for Inference both GPUT P100 for GPUT T4 can be used.

In [1]:
!wget https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Model_VAE.ipynb

--2023-12-13 03:57:09--  https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Model_VAE.ipynb
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 8685 (8.5K) [text/plain]
Saving to: ‘Model_VAE.ipynb’

Model_VAE.ipynb     100%[===================>]   8.48K  --.-KB/s    in 0s      

2023-12-13 03:57:09 (94.4 MB/s) - ‘Model_VAE.ipynb’ saved [8685/8685]



In [2]:
!pip install optuna
import optuna

import h5py
import time
from torch.utils.data import TensorDataset
from sklearn import preprocessing
import numpy as np
import torch
from torch.utils.data import DataLoader

!pip install import-ipynb
import import_ipynb

from google.colab import files
import os

if not os.path.exists("/content/Model_VAE.ipynb"): files.upload()
import Model_VAE as m_vae

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 413.4/413.4 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 230.6/230.6 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 27.6 MB/s eta 0:00:00
importing Jupyter notebook from Model_VAE.ipynb


In [3]:
from importlib import reload
reload(m_vae)

importing Jupyter notebook from Model_VAE.ipynb


<module 'Model_VAE' from 'Model_VAE.ipynb'>

## Dataset

In [4]:
!wget https://github.com/sebascarag/AI-SyntheticSound/raw/main/Resources/vggish_features_labels.hdf5

--2023-12-13 03:57:31--  https://github.com/sebascarag/AI-SyntheticSound/raw/main/Resources/vggish_features_labels.hdf5
Resolving github.com (github.com)... 20.205.243.166
Connecting to github.com (github.com)|20.205.243.166|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Resources/vggish_features_labels.hdf5 [following]
--2023-12-13 03:57:31--  https://raw.githubusercontent.com/sebascarag/AI-SyntheticSound/main/Resources/vggish_features_labels.hdf5
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 29046056 (28M) [application/octet-stream]
Saving to: ‘vggish_features_labels.hdf5’

vggish_features_lab 100%[===================>]  27.70M  --.-KB/s    in 0.08s   

20

In [5]:
with h5py.File('/content/vggish_features_labels.hdf5', 'r') as f:
  data_file = np.array(f.get("data")).astype(float)
print(data_file.shape)
print(type(data_file))
print(data_file[0][0])
print(min(data_file[0]))
print(max(data_file[0]))

(7077, 513)
<class 'numpy.ndarray'>
166.0
0.0
255.0


In [6]:
scaler = preprocessing.MinMaxScaler(feature_range=(0, 1))
features = scaler.fit_transform(data_file[:,:-1])
print("features", features.shape)
print("features", type(features))
print("value",features[0][0])
print("min", min(features[0]))
print("max",max(features[0]))
labels = data_file[:,-1].astype(int)
print("labels", labels.shape)
print("labels", labels[0])

features (7077, 512)
features <class 'numpy.ndarray'>
value 0.4285714285714286
min 0.0
max 1.0
labels (7077,)
labels 2


In [13]:
dataset = TensorDataset( torch.Tensor(features), torch.Tensor(labels) )
x, y = next(enumerate(dataset))
print(x, y)

0 (tensor([0.4286, 0.5763, 0.5957, 0.7378, 1.0000, 0.2713, 0.3596, 0.8250, 1.0000,
        0.4333, 0.4627, 0.3020, 1.0000, 0.5765, 0.0000, 0.0549, 0.6353, 0.2745,
        0.7961, 0.6745, 0.0353, 0.8480, 0.4039, 0.6863, 0.8314, 0.0000, 0.8784,
        0.7686, 0.6706, 0.4667, 0.9059, 0.6314, 0.1294, 0.4549, 0.0510, 0.3843,
        0.6196, 0.8784, 0.9725, 0.6431, 0.2314, 1.0000, 0.6392, 0.0392, 0.3843,
        0.2784, 0.0235, 0.0863, 0.7451, 1.0000, 0.1686, 0.4588, 1.0000, 1.0000,
        0.0000, 0.2000, 0.2471, 0.0000, 0.0000, 0.7961, 0.6000, 0.0000, 0.2784,
        0.5843, 0.9529, 0.9333, 0.7961, 0.6863, 1.0000, 0.6392, 0.1647, 1.0000,
        0.9686, 0.0000, 0.6353, 0.0000, 0.1804, 0.0000, 0.7647, 1.0000, 0.8667,
        1.0000, 0.4235, 0.0000, 0.0000, 1.0000, 1.0000, 1.0000, 0.9176, 0.4235,
        0.0000, 0.0000, 1.0000, 1.0000, 0.6392, 1.0000, 0.9059, 0.0000, 1.0000,
        0.7765, 0.6824, 0.2275, 0.0000, 0.2902, 1.0000, 1.0000, 1.0000, 1.0000,
        1.0000, 1.0000, 1.0000, 1.000

In [7]:
!nvidia-smi -L

GPU 0: Tesla T4 (UUID: GPU-7e007979-acfe-2f56-9006-6a27a0c66272)


In [8]:
!lscpu

Architecture:            x86_64
  CPU op-mode(s):        32-bit, 64-bit
  Address sizes:         46 bits physical, 48 bits virtual
  Byte Order:            Little Endian
CPU(s):                  2
  On-line CPU(s) list:   0,1
Vendor ID:               GenuineIntel
  Model name:            Intel(R) Xeon(R) CPU @ 2.20GHz
    CPU family:          6
    Model:               79
    Thread(s) per core:  2
    Core(s) per socket:  1
    Socket(s):           1
    Stepping:            0
    BogoMIPS:            4399.99
    Flags:               fpu vme de pse tsc msr pae mce cx8 apic sep mtrr pge mca cmov pat pse36 clf
                         lush mmx fxsr sse sse2 ss ht syscall nx pdpe1gb rdtscp lm constant_tsc rep_
                         good nopl xtopology nonstop_tsc cpuid tsc_known_freq pni pclmulqdq ssse3 fm
                         a cx16 pcid sse4_1 sse4_2 x2apic movbe popcnt aes xsave avx f16c rdrand hyp
                         ervisor lahf_lm abm 3dnowprefetch invpcid_single ssbd i

## Optimize v1 - Exploration

* latent_dims=[3-203]
* num_hidden_layers=[150-400]
* learning_rate=[1e-5-1e-2]
* num_epochs=[20-100]
* data scale = [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 3, 203),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 150, 400),
    'random_seed': random_seed
  }
  modelVAE = m_vae.VariationalAutoencoder(**params).to(device)
  return modelVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 1e-5, 1e-2, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 20, 100),
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento en el mismo paso.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pruebas entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_params)

[I 2023-08-13 18:02:44,538] A new study created in memory with name: no-name-5f50f088-1fbd-4dde-bab3-4e9326404be1


Device: cuda:0
Device: cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/030 | Batch 000/589 | kl: 0.2134 + pw: 715.7865 = loss: 715.9999Epoch: 001/043 | Batch 000/589 | kl: 3.4060 + pw: 704.2988 = loss: 707.7048
Epoch: 001/066 | Batch 000/589 | kl: 1.0947 + pw: 719.5812 = loss: 720.6759

Epoch: 001/034 | Batch 000/589 | kl: 1.7905 + pw: 711.8218 = loss: 713.6122
Epoch: 001/030 | Batch 030/589 | kl: 7.9489 + pw: 377.7609 = loss: 385.7098
Epoch: 001/043 | Batch 043/589 | kl: 1.0258 + pw: 455.4559 = loss: 456.4818
Epoch: 001/030 | Batch 060/589 | kl: 10.1150 + pw: 407.2720 = loss: 417.3870
Epoch: 001/030 | Batch 090/589 | kl: 10.9754 + pw: 505.6873 = loss: 516.6627
Epoch: 001/043 | Batch 086/589 | kl: 2.0238 + pw: 715.7446 = loss: 717.7684
Epoch: 001/030 | Batch 120/589 | kl: 8.3626 + pw: 538.2836 = loss: 546.6462
Epoch: 001/043 | Batch 129/589 | kl: 9.7088 + pw: 1006.9633 = loss: 1016.6722
Epoch: 001/030 | Batch 150/589 | kl: 8.2418 + pw: 693.5028 = loss: 701.7446
Epoch: 001/030 | Batch 1

[I 2023-08-13 18:05:17,952] Trial 3 finished with value: 200.79219851736295 and parameters: {'latent_dims': 17, 'num_hidden_layers': 390, 'learning_rate': 0.00017534337318994076, 'num_epochs': 30}. Best is trial 3 with value: 200.79219851736295.


Epoch: 030/030 | Batch 570/589 | kl: 28.0386 + pw: 163.9432 = loss: 191.9818
Time elapsed: 0.09 min
Epoch: 028/043 | Batch 000/589 | kl: 29.4256 + pw: 217.0690 = loss: 246.4946
Time elapsed: 0.08 min
Total Training Time: 2.50 min
Epoch: 020/034 | Batch 374/589 | kl: 28.7141 + pw: 233.5993 = loss: 262.3134
Device: cuda:0
Epoch: 001/031 | Batch 000/589 | kl: 3.2041 + pw: 707.8868 = loss: 711.0909
Epoch: 001/031 | Batch 031/589 | kl: 1.5799 + pw: 215.9385 = loss: 217.5183
Epoch: 020/034 | Batch 408/589 | kl: 27.0936 + pw: 282.7023 = loss: 309.7958
Epoch: 028/043 | Batch 043/589 | kl: 25.1662 + pw: 276.2896 = loss: 301.4558
Epoch: 001/031 | Batch 062/589 | kl: 6.5923 + pw: 450.3247 = loss: 456.9170
Epoch: 009/066 | Batch 528/589 | kl: 14.7657 + pw: 346.6274 = loss: 361.3931
Epoch: 028/043 | Batch 086/589 | kl: 37.1982 + pw: 215.4395 = loss: 252.6377
Epoch: 020/034 | Batch 442/589 | kl: 33.8799 + pw: 252.8199 = loss: 286.6998
Epoch: 001/031 | Batch 093/589 | kl: 1.2512 + pw: 350.2591 = loss

[I 2023-08-13 18:06:45,521] Trial 2 finished with value: 203.40526115934728 and parameters: {'latent_dims': 177, 'num_hidden_layers': 245, 'learning_rate': 0.0006688578452843502, 'num_epochs': 43}. Best is trial 3 with value: 200.79219851736295.


...

Time elapsed: 0.07 min
Prune on epoch: 059 | loss:180.7708
Epoch: 070/094 | Batch 564/589 | kl: 37.8579 + pw: 149.2327 = loss: 187.0906
Epoch: 017/086 | Batch 086/589 | kl: 39.4211 + pw: 175.5764 = loss: 214.9975
Time elapsed: 0.08 min
Epoch: 071/094 | Batch 000/589 | kl: 37.5756 + pw: 169.1348 = loss: 206.7104
Epoch: 017/086 | Batch 172/589 | kl: 32.5448 + pw: 71.6099 = loss: 104.1547
Epoch: 071/094 | Batch 094/589 | kl: 37.5526 + pw: 146.3626 = loss: 183.9152
Epoch: 017/086 | Batch 258/589 | kl: 25.1129 + pw: 120.5110 = loss: 145.6239
Epoch: 071/094 | Batch 188/589 | kl: 40.7348 + pw: 141.4343 = loss: 182.1691
Epoch: 017/086 | Batch 344/589 | kl: 30.6971 + pw: 255.2416 = loss: 285.9387
Epoch: 071/094 | Batch 282/589 | kl: 43.5187 + pw: 153.4668 = loss: 196.9854
Epoch: 017/086 | Batch 430/589 | kl: 32.9877 + pw: 245.3424 = loss: 278.3301
Epoch: 071/094 | Batch 376/589 | kl: 36.6674 + pw: 115.5126 = loss: 152.1801
Epoch: 017/086 | Batch 516/589 | kl: 29.0276 + pw: 274.2599 = loss: 303.

[I 2023-08-13 19:25:48,898] Trial 91 finished with value: 171.4342801821434 and parameters: {'latent_dims': 31, 'num_hidden_layers': 392, 'learning_rate': 0.0002757228954667261, 'num_epochs': 94}. Best is trial 91 with value: 171.4342801821434.


Epoch: 094/094 | Batch 564/589 | kl: 39.0878 + pw: 145.5073 = loss: 184.5951
Time elapsed: 0.05 min
Total Training Time: 9.15 min
Epoch: 038/086 | Batch 430/589 | kl: 38.0912 + pw: 182.1112 = loss: 220.2024
Epoch: 038/086 | Batch 516/589 | kl: 33.4787 + pw: 241.0408 = loss: 274.5194
Time elapsed: 0.05 min
Epoch: 039/086 | Batch 000/589 | kl: 31.3572 + pw: 188.8253 = loss: 220.1825
Epoch: 039/086 | Batch 086/589 | kl: 39.7644 + pw: 132.5633 = loss: 172.3277
Epoch: 039/086 | Batch 172/589 | kl: 34.2611 + pw: 51.2873 = loss: 85.5484
Epoch: 039/086 | Batch 258/589 | kl: 26.3137 + pw: 110.1046 = loss: 136.4183
Epoch: 039/086 | Batch 344/589 | kl: 33.8775 + pw: 209.9179 = loss: 243.7954
Epoch: 039/086 | Batch 430/589 | kl: 39.1881 + pw: 187.1626 = loss: 226.3507
Epoch: 039/086 | Batch 516/589 | kl: 33.3443 + pw: 240.4940 = loss: 273.8383
Time elapsed: 0.03 min
Epoch: 040/086 | Batch 000/589 | kl: 31.3078 + pw: 188.9216 = loss: 220.2294
Epoch: 040/086 | Batch 086/589 | kl: 39.3444 + pw: 128.2

[I 2023-08-13 19:26:25,466] Trial 99 pruned. 


Time elapsed: 0.03 min
Prune on epoch: 059 | loss:180.7454
{'latent_dims': 31, 'num_hidden_layers': 392, 'learning_rate': 0.0002757228954667261, 'num_epochs': 94}


## Results v1

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials))*100 )
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  75
* Complete trials:  25
* %:  25.0
* Best Score:  171.4342801821434
* Best Params by key:  {'latent_dims': 31, 'num_hidden_layers': 392, 'learning_rate': 0.0002757228954667261, 'num_epochs': 94}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number       value             datetime_start          datetime_complete  \
91      91  171.434280 2023-08-13 19:16:39.877115 2023-08-13 19:25:48.897571   
87      87  173.792766 2023-08-13 19:08:07.936214 2023-08-13 19:16:12.166780   
75      75  175.244972 2023-08-13 18:59:25.191718 2023-08-13 19:09:10.134219   
57      57  175.592055 2023-08-13 18:45:04.578420 2023-08-13 18:51:27.658631   
76      76  176.386121 2023-08-13 18:59:27.002550 2023-08-13 19:05:55.933013   
33      33  176.779074 2023-08-13 18:24:01.549154 2023-08-13 18:31:40.124085   
66      66  177.155783 2023-08-13 18:52:34.731949 2023-08-13 18:59:18.951080   
45      45  177.925360 2023-08-13 18:35:45.926459 2023-08-13 18:41:35.291170   
39      39  178.158332 2023-08-13 18:29:56.588903 2023-08-13 18:35:45.921400   
42      42  178.884244 2023-08-13 18:31:27.423891 2023-08-13 18:40:18.912448   
44      44  178.956266 2023-08-13 18:32:29.720686 2023-08-13 18:38:15.714458   
34      34  180.166465 2023-08-13 18:24:31.427077 2023-08-13 18:29:56.581326   
62      62  181.564612 2023-08-13 18:47:10.344000 2023-08-13 18:52:34.727059   
48      48  181.853819 2023-08-13 18:38:39.519392 2023-08-13 18:53:59.301932   
50      50  183.852057 2023-08-13 18:39:22.516229 2023-08-13 18:43:53.580024   
25      25  187.241637 2023-08-13 18:19:01.460770 2023-08-13 18:24:31.423977   
6        6  191.449525 2023-08-13 18:07:06.595172 2023-08-13 18:16:05.561887   
21      21  191.862295 2023-08-13 18:16:05.567080 2023-08-13 18:25:29.199923   
5        5  195.057348 2023-08-13 18:06:45.526125 2023-08-13 18:13:48.050004   
7        7  196.310404 2023-08-13 18:07:54.886604 2023-08-13 18:12:17.760536   
9        9  198.845783 2023-08-13 18:12:45.477799 2023-08-13 18:22:12.796581   
1        1  200.012898 2023-08-13 18:02:44.549730 2023-08-13 18:07:06.590230   
3        3  200.792199 2023-08-13 18:02:44.569936 2023-08-13 18:05:17.951510   
2        2  203.405261 2023-08-13 18:02:44.563116 2023-08-13 18:06:45.520656   
4        4  344.585393 2023-08-13 18:05:17.955268 2023-08-13 18:07:54.879979   

                 duration  params_latent_dims  params_learning_rate  \
91 0 days 00:09:09.020456                  31              0.000276   
87 0 days 00:08:04.230566                  33              0.000387   
75 0 days 00:09:44.942501                  48              0.000439   
57 0 days 00:06:23.080211                  28              0.000375   
76 0 days 00:06:28.930463                  34              0.000430   
33 0 days 00:07:38.574931                  75              0.000458   
66 0 days 00:06:44.219131                  42              0.000459   
45 0 days 00:05:49.364711                  57              0.000437   
39 0 days 00:05:49.332497                  51              0.000414   
42 0 days 00:08:51.488557                  29              0.000331   
44 0 days 00:05:45.993772                  39              0.000418   
34 0 days 00:05:25.154249                  50              0.000471   
62 0 days 00:05:24.383059                  28              0.000539   
48 0 days 00:15:19.782540                  41              0.000360   
50 0 days 00:04:31.063795                  42              0.000260   
25 0 days 00:05:29.963207                  39              0.000795   
6  0 days 00:08:58.966715                  33              0.000803   
21 0 days 00:09:23.632843                  34              0.000830   
5  0 days 00:07:02.523879                  66              0.000797   
7  0 days 00:04:22.873932                 185              0.000176   
9  0 days 00:09:27.318782                  14              0.000296   
1  0 days 00:04:22.040500                 108              0.000339   
3  0 days 00:02:33.381574                  17              0.000175   
2  0 days 00:04:00.957540                 177              0.000669   
4  0 days 00:02:36.924711                 166              0.002093   

    params_num_epochs  params_num_hidden_layers     state  
91              

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number       value                   duration  params_latent_dims  \
count  20.000000   20.000000                         20           20.000000   
mean   45.650000  181.483371  0 days 00:07:19.376100750           49.250000   
std    25.641814    7.215622  0 days 00:02:30.457631638           34.381566   
min     5.000000  171.434280     0 days 00:04:22.873932           28.000000   
25%    31.000000  176.680835  0 days 00:05:41.986130750           33.000000   
50%    44.500000  178.920255     0 days 00:06:36.574797           40.000000   
75%    63.000000  184.699452  0 days 00:08:53.358096500           50.250000   
max    91.000000  196.310404     0 days 00:15:19.782540          185.000000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             20.000000          20.000000                 20.000000  
mean               0.000473          70.800000                341.000000  
std                0.000190          11.455176                 63.370257  
min                0.000176          49.000000                201.000000  
25%                0.000371          64.500000                337.750000  
50%                0.000434          71.500000                368.500000  
75%                0.000488          77.250000                374.500000  
max                0.000830          94.000000                399.000000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Optimize v2 - Explotation

* latent_dims=[10-100] 28-185
* num_hidden_layers=[300-450] 201 - 399
* learning_rate=[1e-4-8.3e-4] 0.000176 - 0.000830
* num_epochs=[49-150] 49 - 94
* data scale = [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 10, 100),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 300, 450),
    'random_seed': random_seed
  }
  modelVAE = m_vae.VariationalAutoencoder(**params).to(device)
  return modelVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 1e-4, 8.3e-4, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 49, 150),
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento en el mismo paso.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pruebas entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_trial.value)
print(study.best_params)

[I 2023-08-13 19:40:04,582] A new study created in memory with name: no-name-fece5139-43a6-4b95-9025-69b99d9aea2a


Device:Device: cuda:0
 cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/074 | Batch 000/589 | kl: 1.6529 + pw: 714.7653 = loss: 716.4182
Epoch: 001/067 | Batch 000/589 | kl: 0.9411 + pw: 714.8440 = loss: 715.7851
Epoch: 001/091 | Batch 000/589 | kl: 0.3178 + pw: 708.2736 = loss: 708.5914
Epoch: 001/123 | Batch 000/589 | kl: 0.8223 + pw: 708.0545 = loss: 708.8768
Epoch: 001/067 | Batch 067/589 | kl: 7.2218 + pw: 413.0118 = loss: 420.2336
Epoch: 001/074 | Batch 074/589 | kl: 7.6819 + pw: 524.5038 = loss: 532.1857
Epoch: 001/067 | Batch 134/589 | kl: 8.9409 + pw: 499.0409 = loss: 507.9818
Epoch: 001/074 | Batch 148/589 | kl: 5.1804 + pw: 410.4837 = loss: 415.6641
Epoch: 001/123 | Batch 123/589 | kl: 5.5711 + pw: 300.8353 = loss: 306.4064
Epoch: 001/091 | Batch 091/589 | kl: 14.1325 + pw: 511.0201 = loss: 525.1526
Epoch: 001/067 | Batch 201/589 | kl: 4.3927 + pw: 695.0422 = loss: 699.4349
Epoch: 001/074 | Batch 222/589 | kl: 4.8790 + pw: 607.0298 = loss: 611.9088
Epoch: 001/067 | Batch 268/

[I 2023-08-13 19:45:37,855] Trial 1 finished with value: 183.2590758695441 and parameters: {'latent_dims': 50, 'num_hidden_layers': 300, 'learning_rate': 0.0002364929913108542, 'num_epochs': 67}. Best is trial 1 with value: 183.2590758695441.


Time elapsed: 0.09 min
Total Training Time: 5.55 min
Device: cuda:0
Epoch: 001/087 | Batch 000/589 | kl: 0.3125 + pw: 711.1892 = loss: 711.5018
Epoch: 061/074 | Batch 370/589 | kl: 40.9739 + pw: 198.6980 = loss: 239.6719
Epoch: 045/123 | Batch 246/589 | kl: 29.4067 + pw: 94.8050 = loss: 124.2117
Epoch: 001/087 | Batch 087/589 | kl: 10.9040 + pw: 485.7300 = loss: 496.6341
Epoch: 061/074 | Batch 444/589 | kl: 40.2821 + pw: 161.5212 = loss: 201.8034
Epoch: 020/091 | Batch 455/589 | kl: 23.2377 + pw: 248.8928 = loss: 272.1305
Epoch: 001/087 | Batch 174/589 | kl: 6.8498 + pw: 522.0839 = loss: 528.9337
Epoch: 061/074 | Batch 518/589 | kl: 36.1459 + pw: 147.6569 = loss: 183.8029
Epoch: 045/123 | Batch 369/589 | kl: 31.0179 + pw: 203.5861 = loss: 234.6041
Epoch: 001/087 | Batch 261/589 | kl: 9.9986 + pw: 269.8865 = loss: 279.8852
Time elapsed: 0.09 min
Epoch: 062/074 | Batch 000/589 | kl: 38.0814 + pw: 177.6435 = loss: 215.7249
Epoch: 062/074 | Batch 074/589 | kl: 53.1642 + pw: 97.4358 = loss:

[I 2023-08-13 19:46:51,943] Trial 3 finished with value: 181.22566079608464 and parameters: {'latent_dims': 84, 'num_hidden_layers': 414, 'learning_rate': 0.00015737352582031599, 'num_epochs': 74}. Best is trial 3 with value: 181.22566079608464.


...

Time elapsed: 0.08 min
Prune on epoch: 071 | loss:174.8685
Epoch: 025/110 | Batch 330/589 | kl: 25.7810 + pw: 189.2695 = loss: 215.0505
Epoch: 030/135 | Batch 405/589 | kl: 25.6234 + pw: 198.6578 = loss: 224.2812
Epoch: 025/110 | Batch 440/589 | kl: 35.8504 + pw: 156.5816 = loss: 192.4320
Epoch: 030/135 | Batch 540/589 | kl: 22.4434 + pw: 225.8921 = loss: 248.3355
Time elapsed: 0.06 min
Epoch: 031/135 | Batch 000/589 | kl: 26.7282 + pw: 195.8143 = loss: 222.5425
Epoch: 025/110 | Batch 550/589 | kl: 36.0016 + pw: 182.1429 = loss: 218.1445
Time elapsed: 0.08 min
Epoch: 026/110 | Batch 000/589 | kl: 31.2990 + pw: 192.3316 = loss: 223.6306
Epoch: 031/135 | Batch 135/589 | kl: 33.4283 + pw: 80.0693 = loss: 113.4976
Epoch: 026/110 | Batch 110/589 | kl: 30.8417 + pw: 157.1767 = loss: 188.0184
Epoch: 031/135 | Batch 270/589 | kl: 22.1735 + pw: 172.4712 = loss: 194.6447
Epoch: 026/110 | Batch 220/589 | kl: 31.3407 + pw: 89.6481 = loss: 120.9887
Epoch: 031/135 | Batch 405/589 | kl: 26.9183 + pw:

[I 2023-08-13 22:12:10,376] Trial 99 pruned. 


Time elapsed: 0.05 min
Prune on epoch: 032 | loss:193.7196
Epoch: 028/110 | Batch 330/589 | kl: 26.8892 + pw: 189.8918 = loss: 216.7811
Epoch: 028/110 | Batch 440/589 | kl: 34.6409 + pw: 155.9793 = loss: 190.6203
Epoch: 028/110 | Batch 550/589 | kl: 35.4058 + pw: 179.5899 = loss: 214.9957
Time elapsed: 0.04 min
Epoch: 029/110 | Batch 000/589 | kl: 32.1418 + pw: 189.0339 = loss: 221.1756
Epoch: 029/110 | Batch 110/589 | kl: 30.4497 + pw: 154.0283 = loss: 184.4780
Epoch: 029/110 | Batch 220/589 | kl: 32.0331 + pw: 89.2413 = loss: 121.2744
Epoch: 029/110 | Batch 330/589 | kl: 26.1029 + pw: 186.1360 = loss: 212.2389
Epoch: 029/110 | Batch 440/589 | kl: 35.6751 + pw: 157.0649 = loss: 192.7400
Epoch: 029/110 | Batch 550/589 | kl: 36.2364 + pw: 177.5384 = loss: 213.7748
Time elapsed: 0.03 min
Epoch: 030/110 | Batch 000/589 | kl: 31.5345 + pw: 188.9906 = loss: 220.5251
Epoch: 030/110 | Batch 110/589 | kl: 30.0556 + pw: 151.6550 = loss: 181.7106
Epoch: 030/110 | Batch 220/589 | kl: 32.3166 + pw

[I 2023-08-13 22:13:03,931] Trial 96 pruned. 


Epoch: 060/110 | Batch 550/589 | kl: 37.6428 + pw: 161.3318 = loss: 198.9745
Time elapsed: 0.03 min
Prune on epoch: 059 | loss:178.1199
{'latent_dims': 38, 'num_hidden_layers': 436, 'learning_rate': 0.0003167601096782904, 'num_epochs': 140}


## Results v2

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials))*100 )
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  80
* Complete trials:  20
* %:  20.0
* Best Score:  164.75252566580045
* Best Params by key:  {'latent_dims': 38, 'num_hidden_layers': 436, 'learning_rate': 0.0003167601096782904, 'num_epochs': 140}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number       value             datetime_start          datetime_complete  \
87      87  164.752526 2023-08-13 21:56:21.976896 2023-08-13 22:08:03.822060   
28      28  165.004584 2023-08-13 20:36:41.203803 2023-08-13 20:49:30.905229   
5        5  165.142091 2023-08-13 19:46:51.950074 2023-08-13 20:00:32.719405   
56      56  165.327051 2023-08-13 21:14:38.474626 2023-08-13 21:25:46.707237   
19      19  165.918635 2023-08-13 20:05:27.165021 2023-08-13 20:16:22.899425   
22      22  166.045488 2023-08-13 20:16:22.905603 2023-08-13 20:27:45.051041   
64      64  166.672586 2023-08-13 21:31:09.441044 2023-08-13 21:46:36.716447   
31      31  166.675969 2023-08-13 20:44:10.540992 2023-08-13 20:54:02.641444   
30      30  166.869098 2023-08-13 20:38:43.097657 2023-08-13 20:53:45.045532   
45      45  167.181618 2023-08-13 20:58:19.309193 2023-08-13 21:07:50.537183   
77      77  167.273582 2023-08-13 21:47:23.160715 2023-08-13 22:01:23.205951   
48      48  168.242731 2023-08-13 21:05:20.855912 2023-08-13 21:14:47.009600   
24      24  169.144379 2023-08-13 20:18:12.739848 2023-08-13 20:28:23.200765   
0        0  171.216098 2023-08-13 19:40:04.586363 2023-08-13 19:55:29.928074   
8        8  176.430384 2023-08-13 19:58:48.363044 2023-08-13 20:05:27.158090   
6        6  179.547683 2023-08-13 19:52:47.785910 2023-08-13 19:58:48.357934   
3        3  181.225661 2023-08-13 19:40:04.594144 2023-08-13 19:46:51.943024   
1        1  183.259076 2023-08-13 19:40:04.589144 2023-08-13 19:45:37.854735   
4        4  183.821895 2023-08-13 19:45:37.861215 2023-08-13 19:52:47.780307   
7        7  184.297820 2023-08-13 19:55:29.932771 2023-08-13 20:02:08.308177   

                 duration  params_latent_dims  params_learning_rate  \
87 0 days 00:11:41.845164                  38              0.000317   
28 0 days 00:12:49.701426                  38              0.000275   
5  0 days 00:13:40.769331                  93              0.000183   
56 0 days 00:11:08.232611                  32              0.000298   
19 0 days 00:10:55.734404                  37              0.000294   
22 0 days 00:11:22.145438                  24              0.000391   
64 0 days 00:15:27.275403                  33              0.000322   
31 0 days 00:09:52.100452                  34              0.000321   
30 0 days 00:15:01.947875                  44              0.000281   
45 0 days 00:09:31.227990                  36              0.000241   
77 0 days 00:14:00.045236                  34              0.000291   
48 0 days 00:09:26.153688                  46              0.000307   
24 0 days 00:10:10.460917                  55              0.000382   
0  0 days 00:15:25.341711                  61              0.000311   
8  0 days 00:06:38.795046                  43              0.000432   
6  0 days 00:06:00.572024                  81              0.000484   
3  0 days 00:06:47.348880                  84              0.000157   
1  0 days 00:05:33.265591                  50              0.000236   
4  0 days 00:07:09.919092                  15              0.000248   
7  0 days 00:06:38.375406                  40              0.000218   

    params_num_epochs  params_num_hidden_layers     state  
87                140                       436  COMPLETE  
28                139                       434  COMPLETE  
5                 148                       434  COMPLETE  
56                134                       428  COMPLETE  
19                132                       423  COMPLETE  
22                137                       424  COMPLETE  
64                122                       434  COMPLETE  
31                119                       439  COMPLETE  
30                119                       432  COMPLETE  
45                114                       442  COMPLETE  
77                111                       433  COMPLETE  
48                101                       450  COMPLETE  
24                110                       429  CO

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number       value                   duration  params_latent_dims  \
count  20.000000   20.000000                         20           20.000000   
mean   28.250000  171.202448  0 days 00:10:28.062884250           45.900000   
std    26.520846    7.195401  0 days 00:03:15.504240594           20.073287   
min     0.000000  164.752526     0 days 00:05:33.265591           15.000000   
25%     5.750000  166.013774     0 days 00:07:04.276539           34.000000   
50%    23.000000  167.227600  0 days 00:10:33.097660500           39.000000   
75%    45.750000  177.209709  0 days 00:13:02.468402250           51.250000   
max    87.000000  184.297820     0 days 00:15:27.275403           93.000000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             20.000000          20.000000                 20.000000  
mean               0.000300         109.100000                405.800000  
std                0.000079          27.907554                 46.260817  
min                0.000157          53.000000                300.000000  
25%                0.000246          85.250000                385.500000  
50%                0.000296         116.500000                428.500000  
75%                0.000322         132.500000                434.000000  
max                0.000484         148.000000                450.000000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Optimize v3 - Explotation

* latent_dims=[15-60]
* num_hidden_layers=[390-490]
* learning_rate=[2e-4-4e-4]
* num_epochs=[90-200]
* data scale = [0-1]
* batch_size = 12

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 12, shuffle = False)

def create_model(trial):
  params = {
    'latent_dims': trial.suggest_int('latent_dims', 15, 60),
    'num_features': 512,
    'num_hidden_layers': trial.suggest_int('num_hidden_layers', 390, 490),
    'random_seed': random_seed
  }
  modelVAE = m_vae.VariationalAutoencoder(**params).to(device)
  return modelVAE

def objective(trial):
  model = create_model(trial)
  # <ipython-input-10-6b59815d81c9>:31: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0.
  # See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead. 'learning_rate': trial.suggest_loguniform('learning_rate', 1e-5, 1e-2),
  params = {
    'data': data,
    'learning_rate': trial.suggest_float('learning_rate', 2e-4, 4e-4, log=True),
    'num_epochs': trial.suggest_int('num_epochs', 90, 200),
    'optuna_trial': trial
  }
  best_model, best_loss, losses = model.train_fit(**params)
  return best_loss

study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner( # MedianPruner: se centra en los resultados anteriores y elimina las combinaciones que se encuentren por debajo de la mediana de los resultados obtenidos hasta ese momento en el mismo paso.
        #n_startup_trials=2, # ignorando los resultados de las dos primeras pruebas
        n_warmup_steps=5, # nro de pruebas antes de comenzar a aplicar la poda.
        interval_steps=3 # intervalo de pruebas entre las aplicaciones de la poda
    ), direction="minimize")

# n_jobs: pruebas paralelas
study.optimize(objective, n_trials=100, n_jobs=4)

print(study.best_trial.value)
print(study.best_params)

[I 2023-08-14 04:17:04,861] A new study created in memory with name: no-name-c8041705-ebc7-4284-ab6e-2b3ea373014b


Device: cuda:0
Device: cuda:0
Device: cuda:0
Device: cuda:0
Epoch: 001/098 | Batch 000/589 | kl: 0.7382 + pw: 711.5906 = loss: 712.3289
Epoch: 001/094 | Batch 000/589 | kl: 0.4107 + pw: 711.9980 = loss: 712.4087
Epoch: 001/120 | Batch 000/589 | kl: 0.2751 + pw: 720.2061 = loss: 720.4812
Epoch: 001/161 | Batch 000/589 | kl: 0.7654 + pw: 711.0601 = loss: 711.8254
Epoch: 001/094 | Batch 094/589 | kl: 5.1919 + pw: 473.2907 = loss: 478.4826
Epoch: 001/098 | Batch 098/589 | kl: 1.9824 + pw: 415.0928 = loss: 417.0752
Epoch: 001/094 | Batch 188/589 | kl: 5.3408 + pw: 483.1755 = loss: 488.5164
Epoch: 001/161 | Batch 161/589 | kl: 3.5849 + pw: 438.0757 = loss: 441.6606
Epoch: 001/094 | Batch 282/589 | kl: 7.0474 + pw: 575.9297 = loss: 582.9771
Epoch: 001/098 | Batch 196/589 | kl: 8.9970 + pw: 423.6999 = loss: 432.6968
Epoch: 001/120 | Batch 120/589 | kl: 6.9149 + pw: 542.4403 = loss: 549.3552
Epoch: 001/161 | Batch 322/589 | kl: 10.5371 + pw: 362.9761 = loss: 373.5132
Epoch: 001/094 | Batch 376/

[I 2023-08-14 04:24:59,077] Trial 3 finished with value: 172.86521708601612 and parameters: {'latent_dims': 22, 'num_hidden_layers': 397, 'learning_rate': 0.0003055447235943878, 'num_epochs': 94}. Best is trial 3 with value: 172.86521708601612.


Time elapsed: 0.08 min
Total Training Time: 7.85 min
Device: cuda:0
Epoch: 001/121 | Batch 000/589 | kl: 0.3736 + pw: 708.5360 = loss: 708.9097
Epoch: 063/098 | Batch 392/589 | kl: 40.2080 + pw: 153.5530 = loss: 193.7610
Epoch: 001/121 | Batch 121/589 | kl: 2.7434 + pw: 580.3489 = loss: 583.0922
Epoch: 085/161 | Batch 483/589 | kl: 35.2116 + pw: 144.3403 = loss: 179.5519
Epoch: 063/098 | Batch 490/589 | kl: 37.1432 + pw: 157.9146 = loss: 195.0578
Epoch: 001/121 | Batch 242/589 | kl: 6.8544 + pw: 369.1595 = loss: 376.0139
Time elapsed: 0.09 min
Epoch: 086/161 | Batch 000/589 | kl: 37.7609 + pw: 161.3471 = loss: 199.1080
Epoch: 063/098 | Batch 588/589 | kl: 33.5647 + pw: 172.5285 = loss: 206.0932
Time elapsed: 0.12 min
Epoch: 064/098 | Batch 000/589 | kl: 34.2494 + pw: 168.8430 = loss: 203.0925
Epoch: 030/120 | Batch 240/589 | kl: 35.4519 + pw: 201.9861 = loss: 237.4380
Epoch: 001/121 | Batch 363/589 | kl: 3.2491 + pw: 138.8688 = loss: 142.1180
Epoch: 086/161 | Batch 161/589 | kl: 33.704

[I 2023-08-14 04:29:25,929] Trial 1 finished with value: 167.90250018491582 and parameters: {'latent_dims': 49, 'num_hidden_layers': 485, 'learning_rate': 0.00032620204219902595, 'num_epochs': 98}. Best is trial 1 with value: 167.90250018491582.


...

Time elapsed: 0.08 min
Prune on epoch: 098 | loss:168.2101
Epoch: 089/121 | Batch 121/589 | kl: 38.0325 + pw: 98.2272 = loss: 136.2598
Epoch: 070/098 | Batch 294/589 | kl: 39.4857 + pw: 95.8783 = loss: 135.3640
Epoch: 089/121 | Batch 242/589 | kl: 35.4622 + pw: 149.9592 = loss: 185.4214
Epoch: 070/098 | Batch 392/589 | kl: 42.3818 + pw: 143.1629 = loss: 185.5446
Epoch: 089/121 | Batch 363/589 | kl: 24.5993 + pw: 7.6880 = loss: 32.2873
Epoch: 070/098 | Batch 490/589 | kl: 36.6578 + pw: 157.9334 = loss: 194.5912
Epoch: 070/098 | Batch 588/589 | kl: 37.2453 + pw: 164.9026 = loss: 202.1479
Time elapsed: 0.07 min
Epoch: 071/098 | Batch 000/589 | kl: 38.1865 + pw: 161.8919 = loss: 200.0784
Epoch: 089/121 | Batch 484/589 | kl: 32.8280 + pw: 102.4057 = loss: 135.2337
Epoch: 071/098 | Batch 098/589 | kl: 35.0591 + pw: 159.8864 = loss: 194.9454
Time elapsed: 0.06 min
Epoch: 090/121 | Batch 000/589 | kl: 38.1837 + pw: 159.1300 = loss: 197.3137
Epoch: 071/098 | Batch 196/589 | kl: 34.2203 + pw: 11

[I 2023-08-14 06:20:11,124] Trial 82 finished with value: 167.44990668862553 and parameters: {'latent_dims': 30, 'num_hidden_layers': 482, 'learning_rate': 0.0002987983510135402, 'num_epochs': 98}. Best is trial 10 with value: 159.50640869787185.


Epoch: 098/098 | Batch 588/589 | kl: 38.0594 + pw: 161.4010 = loss: 199.4604
Time elapsed: 0.06 min
Total Training Time: 19.58 min
Epoch: 120/121 | Batch 484/589 | kl: 32.3867 + pw: 96.9167 = loss: 129.3034
Time elapsed: 0.04 min
Epoch: 121/121 | Batch 000/589 | kl: 37.9764 + pw: 148.3137 = loss: 186.2901
Epoch: 121/121 | Batch 121/589 | kl: 40.2785 + pw: 91.4502 = loss: 131.7287
Epoch: 121/121 | Batch 242/589 | kl: 38.1586 + pw: 141.4886 = loss: 179.6472
Epoch: 121/121 | Batch 363/589 | kl: 25.1465 + pw: 7.3197 = loss: 32.4662
Epoch: 121/121 | Batch 484/589 | kl: 34.3624 + pw: 97.2124 = loss: 131.5748


[I 2023-08-14 06:20:13,210] Trial 93 finished with value: 164.2278857796879 and parameters: {'latent_dims': 38, 'num_hidden_layers': 487, 'learning_rate': 0.0003116067045281155, 'num_epochs': 121}. Best is trial 10 with value: 159.50640869787185.


Time elapsed: 0.03 min
Total Training Time: 12.44 min
159.50640869787185
{'latent_dims': 42, 'num_hidden_layers': 483, 'learning_rate': 0.0002779903927778435, 'num_epochs': 176}


## Results v3

In [ ]:
prunedTrials = len(study.get_trials(states=[optuna.trial.TrialState.PRUNED]))
completeTrials = len(study.get_trials(states=[optuna.trial.TrialState.COMPLETE]))
print("* Pruned trials: ", prunedTrials)
print("* Complete trials: ", completeTrials)
print("* %: ", (completeTrials / (prunedTrials + completeTrials)) * 100)
print("* Best Score: ", study.best_trial.value)
print("* Best Params by key: ", study.best_params)

* Pruned trials:  88
* Complete trials:  12
* %:  12.0
* Best Score:  159.50640869787185
* Best Params by key:  {'latent_dims': 42, 'num_hidden_layers': 483, 'learning_rate': 0.0002779903927778435, 'num_epochs': 176}


In [ ]:
df_best = study.trials_dataframe().sort_values(by="value")
df_best = df_best[df_best.state == "COMPLETE"]
df_best

number       value             datetime_start          datetime_complete  \
10      10  159.506409 2023-08-14 04:44:01.282087 2023-08-14 05:06:05.414491   
2        2  161.193681 2023-08-14 04:17:04.874067 2023-08-14 04:32:01.113006   
93      93  164.227886 2023-08-14 06:07:46.648245 2023-08-14 06:20:13.210062   
72      72  165.750576 2023-08-14 05:48:15.942225 2023-08-14 05:57:14.669058   
80      80  166.021325 2023-08-14 05:57:57.512578 2023-08-14 06:08:04.332108   
66      66  166.772614 2023-08-14 05:32:24.353595 2023-08-14 05:41:54.317165   
4        4  167.090603 2023-08-14 04:24:59.079901 2023-08-14 04:35:02.438813   
82      82  167.449907 2023-08-14 06:00:35.951245 2023-08-14 06:20:11.123388   
1        1  167.902500 2023-08-14 04:17:04.871464 2023-08-14 04:29:25.928624   
56      56  168.057725 2023-08-14 05:23:05.641990 2023-08-14 05:31:12.591200   
7        7  170.446721 2023-08-14 04:35:02.442072 2023-08-14 04:43:50.818191   
3        3  172.865217 2023-08-14 04:17:04.876216 2023-08-14 04:24:59.076670   

                 duration  params_latent_dims  params_learning_rate  \
10 0 days 00:22:04.132404                  42              0.000278   
2  0 days 00:14:56.238939                  56              0.000282   
93 0 days 00:12:26.561817                  38              0.000312   
72 0 days 00:08:58.726833                  33              0.000285   
80 0 days 00:10:06.819530                  32              0.000268   
66 0 days 00:09:29.963570                  29              0.000285   
4  0 days 00:10:03.358912                  29              0.000307   
82 0 days 00:19:35.172143                  30              0.000299   
1  0 days 00:12:21.057160                  49              0.000326   
56 0 days 00:08:06.949210                  28              0.000290   
7  0 days 00:08:48.376119                  53              0.000233   
3  0 days 00:07:54.200454                  22              0.000306   

    params_num_epochs  params_num_hidden_layers     state  
10                176                       483  COMPLETE  
2                 161                       482  COMPLETE  
93                121                       487  COMPLETE  
72                107                       490  COMPLETE  
80                110                       483  COMPLETE  
66                103                       483  COMPLETE  
4                 121                       428  COMPLETE  
82                 98                       482  COMPLETE  
1                  98                       485  COMPLETE  
56                 97                       486  COMPLETE  
7                 106                       402  COMPLETE  
3                  94                       397  COMPLETE

In [ ]:
if completeTrials > 20:
    df_best = df_best.head(20).describe()
else:
    df_best = df_best.describe()
df_best

number       value                   duration  params_latent_dims  \
count  12.000000   12.000000                         12           12.000000   
mean   39.666667  166.440430  0 days 00:12:04.296424250           36.750000   
std    37.835369    3.628042  0 days 00:04:35.908562064           10.913919   
min     1.000000  159.506409     0 days 00:07:54.200454           22.000000   
25%     3.750000  165.369904  0 days 00:08:56.139154500           29.000000   
50%    33.000000  166.931609     0 days 00:10:05.089221           32.500000   
75%    74.000000  167.941306  0 days 00:13:03.981097500           43.750000   
max    93.000000  172.865217     0 days 00:22:04.132404           56.000000   

       params_learning_rate  params_num_epochs  params_num_hidden_layers  
count             12.000000          12.000000                 12.000000  
mean               0.000289         116.000000                465.666667  
std                0.000024          26.205482                 34.976182  
min                0.000233          94.000000                397.000000  
25%                0.000281          98.000000                468.500000  
50%                0.000287         106.500000                483.000000  
75%                0.000306         121.000000                485.250000  
max                0.000326         176.000000                490.000000

In [ ]:
optuna.visualization.plot_slice(study)

In [ ]:
optuna.visualization.plot_param_importances(study)

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
optuna.visualization.plot_rank(study)

In [ ]:
optuna.visualization.plot_intermediate_values(study)

In [ ]:
optuna.visualization.plot_timeline(study)

## Best params with batch size 8 - Refining


* Best Score:  159.50640869787185
* Best Params by key:  {'latent_dims': 42, 'num_hidden_layers': 483, 'learning_rate': 0.0002779903927778435, 'num_epochs': 176}

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 8, shuffle = False)

params = {
    'latent_dims': 42,
    'num_features': 512,
    'num_hidden_layers': 483,
    'random_seed': random_seed
}
modelVAE = m_vae.VariationalAutoencoder(**params).to(device)

params = {
    'data': data,
    'learning_rate': 0.0002779903927778435,
    'num_epochs': 176
}
best_model, best_loss, losses = modelVAE.train_fit(**params)

print(best_loss)

Device: cuda:0
Epoch: 001/176 | Batch 000/884 | kl: 0.8507 + pw: 380.4203 = loss: 381.2710
Epoch: 001/176 | Batch 176/884 | kl: 1.6647 + pw: 329.6158 = loss: 331.2805
Epoch: 001/176 | Batch 352/884 | kl: 5.2113 + pw: 269.3337 = loss: 274.5450
Epoch: 001/176 | Batch 528/884 | kl: 3.6451 + pw: 277.1805 = loss: 280.8257
Epoch: 001/176 | Batch 704/884 | kl: 6.9391 + pw: 228.0551 = loss: 234.9942
Epoch: 001/176 | Batch 880/884 | kl: 8.6449 + pw: 173.9694 = loss: 182.6143
Time elapsed: 0.07 min
Epoch: 002/176 | Batch 000/884 | kl: 11.4361 + pw: 226.6363 = loss: 238.0724
Epoch: 002/176 | Batch 176/884 | kl: 12.1499 + pw: 264.9852 = loss: 277.1351
Epoch: 002/176 | Batch 352/884 | kl: 12.0686 + pw: 221.9848 = loss: 234.0533
Epoch: 002/176 | Batch 528/884 | kl: 9.1791 + pw: 248.2401 = loss: 257.4192
Epoch: 002/176 | Batch 704/884 | kl: 10.9574 + pw: 213.8161 = loss: 224.7734
Epoch: 002/176 | Batch 880/884 | kl: 9.7304 + pw: 170.8720 = loss: 180.6024
Time elapsed: 0.04 min
Epoch: 003/176 | Batch 

## Best params with batch size 4 - Refining

* Best Score:  159.50640869787185
* Best Params by key:  {'latent_dims': 42, 'num_hidden_layers': 483, 'learning_rate': 0.0002779903927778435, 'num_epochs': 176}

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

random_seed = 4

torch.manual_seed(random_seed)
data = DataLoader( dataset, batch_size = 4, shuffle = False)

params = {
    'latent_dims': 42,
    'num_features': 512,
    'num_hidden_layers': 483,
    'random_seed': random_seed
}
modelVAE = m_vae.VariationalAutoencoder(**params).to(device)

params = {
    'data': data,
    'learning_rate': 0.0002779903927778435,
    'num_epochs': 176
}
best_model, best_loss, losses = modelVAE.train_fit(**params)

print(best_loss)

Device: cuda:0
Epoch: 001/176 | Batch 000/1769 | kl: 0.8239 + pw: 181.0216 = loss: 181.8456
Epoch: 001/176 | Batch 176/1769 | kl: 0.8458 + pw: 202.6616 = loss: 203.5074
Epoch: 001/176 | Batch 352/1769 | kl: 1.8908 + pw: 148.2818 = loss: 150.1726
Epoch: 001/176 | Batch 528/1769 | kl: 2.5148 + pw: 130.5522 = loss: 133.0670
Epoch: 001/176 | Batch 704/1769 | kl: 3.3125 + pw: 121.3202 = loss: 124.6328
Epoch: 001/176 | Batch 880/1769 | kl: 7.1184 + pw: 162.7892 = loss: 169.9076
Epoch: 001/176 | Batch 1056/1769 | kl: 1.9099 + pw: 128.7176 = loss: 130.6275
Epoch: 001/176 | Batch 1232/1769 | kl: 5.9411 + pw: 130.2113 = loss: 136.1524
Epoch: 001/176 | Batch 1408/1769 | kl: 3.4094 + pw: 131.8032 = loss: 135.2126
Epoch: 001/176 | Batch 1584/1769 | kl: 5.4283 + pw: 126.8314 = loss: 132.2597
Epoch: 001/176 | Batch 1760/1769 | kl: 6.0777 + pw: 95.5929 = loss: 101.6706
Time elapsed: 0.08 min
Epoch: 002/176 | Batch 000/1769 | kl: 6.3573 + pw: 105.0909 = loss: 111.4482
Epoch: 002/176 | Batch 176/1769 | 